# Costa Rica Pipeline Notebook

This is the `Classification Data Cleaning and EDA` section of the notebook where:

- Data imported from `"Costa_Rica_Data/Setup Output"` (both Spanish and English versions)
- Creation of a generic single point-per-plot GeoDataFrame with statistical columns on %forest, %agriculture, %every other Uso class, etc. per plot (**`TODO`**)
- An Exploratory Data Analysis (using `gdf_s`) focused on:
    1. Analyzing plots and points, identifying their NA values, and detecting/removing duplicate entries
    2. Visualizations for showing %UseType cover (**`TODO`**)
    3. Calculation of descriptive statistics for %UseType (i.e. `min, max, mean, std dev, std err, confidence interval`) using the single point-per-plot GeoDataFrame (**`TODO`**)
    4. Replacing NA values in columsn with `"Not_Applicable"` or their Spanish alternative `"No_Aplicable"`

> Note: All changes done to `gdf_s` are also done to `gdf_e` (e.g. Removing duplicate entries and replacing NA values)

## Section 1 - Setup

### Section 1.1 - Installing software and importing packages

In [267]:
!pip install pandas numpy geopandas seaborn scikit-learn tensor folium matplotlib mapclassify earthengine-api geemap pyarrow

In [268]:
from IPython.core.display import display_webp
from geopandas import GeoDataFrame
from shapely.geometry import Point
import geopandas as gpd
import pandas as pd
import numpy as np
import geemap
import ee
import folium
import matplotlib.pyplot as plt
import seaborn as sns
import pyarrow

### Section 1.2 - Importing our Dataset

In [269]:
# We are importing the observational data from the ZIP file provided (which contains the shape file) into a GeoDataFrame
gdf_s = gpd.read_parquet('../Costa_Rica_Data/Setup Output/sp_setup_data.parquet')
gdf_e = gpd.read_parquet('../Costa_Rica_Data/Setup Output/en_setup_data.parquet')

# These display information about the GeoDataFrame to confirm the contains are what we expected
display(gdf_s.columns)
display(gdf_e.columns)

# Confirming that these are GeoDataFrames
display(type(gdf_s))
display(type(gdf_e))

Index(['plotid', 'sampleid', 'Uso', 'Cobertura', 'Vegetacion', 'Herbaceas',
       'Pasto_Arb', 'Cultivo', 'Humedal', 'Terreno', 'Agua', 'Otra_clase',
       'SAF', 'Cambios15_', 'Gana_Perdi', 'geometry'],
      dtype='object')

Index(['plotid', 'sampleid', 'Use', 'CoverType', 'Vegetations', 'Herbaceous',
       'GrasslandShrub', 'CropsType', 'WetlandArea', 'LandType',
       'WaterBodyType', 'OtherClass', 'SAF', 'Changes_15', 'Gain_Loss',
       'geometry'],
      dtype='object')

geopandas.geodataframe.GeoDataFrame

geopandas.geodataframe.GeoDataFrame

## Section 2 - Data Acquisition and Cleaning

### Section 2.1 - Points imported, and points turned into "wide" format for the "9->1 row per plot conversion

In [270]:
# Insert code here for Section 2.1

### Section 2.2 - Exploratory Data Analysis (EDA)

#### Section 2.2.1 Exploration of Plots and Points

In [271]:
# Count of points, count of plots, and ID of NA's (if appropriate).

# Reworked solution - Convert columns to objects and get those statistics instead of the numerical ones
plotid_obj_stats = (gdf_s['plotid'].astype('object')).describe()
sampleid_obj_stats = (gdf_s['sampleid'].astype('object')).describe()

# Combine above results into a single dataframe
results_df = pd.concat([plotid_obj_stats, sampleid_obj_stats], axis=1)

# Check for NAs in each column and append to dataframe
results_df.loc["Has NAs"] = [str(gdf_s['plotid'].isna().any()), str(gdf_s['sampleid'].isna().any())]

# Display results
display(results_df)

plotid sampleid
count    101160   101160
unique    11233    49469
top        3105    12425
freq         18        4
Has NAs   False    False

In summary, out of the **101,160 rows of data** in our Dataframe, there are only:
- 11,233 unique plots,
- 49,469 unique sampleids (points).

However, you can notice that the highest frequency for sampleids is more than 1, which means there are sampleids being used more than once.

> Question 1: How many sampleids (points) are being used more than one time?

Also, there are no NA values in these two columns.

In [272]:
# Count of plots that have fewer than 9 points per plot (and why)

# Create subsets of gdf_s where the frequency of the plotid/sampleid is calculated
plotid_counts = pd.DataFrame(gdf_s['plotid'].value_counts(dropna=False))
sampleid_counts = pd.DataFrame(gdf_s['sampleid'].value_counts(dropna=False))

# Creates subsets of sampleid_counts that counts the frequency of each points' frequency
sampleid_counts_mt0 = sampleid_counts[sampleid_counts['count'] > 0]
sampleid_counts_frequency = pd.DataFrame(sampleid_counts_mt0['count'].value_counts())
sampleid_counts_frequency.rename(columns={ sampleid_counts_frequency.columns[0]: "count frequency" }, inplace=True)

print("There are {number_of_rows} plotid's with less than 9 points per plot:".format(number_of_rows=len(plotid_counts[plotid_counts['count'] < 9])))
display(plotid_counts[plotid_counts['count'] < 9])

print("There are {number_of_rows} plotid's with more than 9 points per plot:".format(number_of_rows=len(plotid_counts[plotid_counts['count'] > 9])))
display(plotid_counts[plotid_counts['count'] > 9])

# This answers Question 1: "How many sampleids (points) are being used more than one time?"
print("There are {number_of_rows} points that appear more than once:".format(number_of_rows=len(sampleid_counts[sampleid_counts['count'] > 1])))
display(sampleid_counts_frequency)

There are 0 plotid's with less than 9 points per plot:


Empty DataFrame
Columns: [count]
Index: []

There are 7 plotid's with more than 9 points per plot:


count
plotid       
3105       18
3150       18
6916       18
1630       18
3163       18
4607       18
2175       18

There are 41437 points that appear more than once:


count frequency
count                 
2                31204
3                10212
1                 8032
4                   21

In summary, out of all the unique plots in our data:
- **None** have less than nine points per plot
- **Seven** have more than nine points per plot (exactly 18 in fact)

> Question 2: Why do those seven plots have 18 points instead of nine?

> Question 3: Are all 18 of those points unique, or are some of them repeated?

##### **Recall Question 1: "How many sampleids (points) are being used more than one time?"**

Out of all the sampleids (points) in our data:
- **21** appear four times
- **10,212** three times
- **31,204** appear two times
- **8,032** appear one time

> Question 4: Are there sampleids that are associated with **more than one** unique geometric point?

In [273]:
# This answers Question 2: "Why do those seven plots have 18 points instead of nine?"
# Also Question 3: "Are all 18 of those points unique, or are some of them repeated?"

"""
This function groups a DataFrame by `id_name`, checks if the `associated_id` values in each group are unique, and returns:
1) A DataFrame with all groups and their uniqueness status.
2) A filtered DataFrame showing only groups with duplicate `associated_id` values.
"""
def analyze_ids(df, id_name, associated_id):
    # Filter 'sampleid' values where 'geometry' equals a specific value
    result = df.groupby(id_name)[associated_id].apply(list)

    # Create a new DataFrame from the result
    result_df = result.reset_index(name=(associated_id + "_list"))

    # Add a column to check if all sampleid values are unique
    result_df['all_unique'] = result_df[associated_id + "_list"].apply(lambda x: len(x) == len(set(x)))

    # Filter rows where all_unique == False
    duplicated_rows = result_df[result_df['all_unique'] == False].copy()

    # Adjust the sampleid_list column to show only duplicated values
    duplicated_rows['duplicated_' + associated_id] = duplicated_rows[associated_id + "_list"].apply(
        lambda x: [item for item in set(x) if x.count(item) > 1]
    )

    return result_df, duplicated_rows[[id_name, 'duplicated_' + associated_id]]

# Use the defined function above to check which sampleids are associated with which plotid
results_df, duplicates_df = analyze_ids(gdf_s, "plotid", "sampleid")

# Display the results
display(results_df[results_df['all_unique'] == False])
display(duplicates_df)

plotid                                      sampleid_list  all_unique
1610    1630  [6517, 6517, 6518, 6518, 6519, 6519, 6520, 652...       False
2153    2175  [8697, 8697, 8698, 8698, 8699, 8699, 8700, 870...       False
3082    3105  [12417, 12417, 12418, 12418, 12419, 12419, 124...       False
3127    3150  [12597, 12597, 12598, 12598, 12599, 12599, 126...       False
3140    3163  [12649, 12649, 12650, 12650, 12651, 12651, 126...       False
4584    4607  [18425, 18425, 18426, 18426, 18427, 18427, 184...       False
6893    6916  [27661, 27661, 27662, 27662, 27663, 27663, 276...       False

plotid                                duplicated_sampleid
1610    1630  [6517, 6518, 6519, 6520, 6521, 6522, 6523, 652...
2153    2175  [8704, 8705, 8697, 8698, 8699, 8700, 8701, 870...
3082    3105  [12417, 12418, 12419, 12420, 12421, 12422, 124...
3127    3150  [12597, 12598, 12599, 12600, 12601, 12602, 126...
3140    3163  [12649, 12650, 12651, 12652, 12653, 12654, 126...
4584    4607  [18432, 18433, 18425, 18426, 18427, 18428, 184...
6893    6916  [27661, 27662, 27663, 27664, 27665, 27666, 276...

##### **Recall Questions 2 & 3: "Why do those seven plots have 18 points instead of nine; also, are all 18 of those points unique, or are some of them repeated?"**
Visually, we can tell that these seven plots:
- Have had 9 sampleid's counted twice,
- Do not have all associated sampleid's unique.

> Question TODO: In those seven plotids with 18 sampleids, do the duplicated sampleids contain the same information?

In [274]:
# This answers Question 4: "Are there sampleids that are associated with more than one unique geometric point?"

# Call the analyze_ids function to analyze the values of each sampleid and determine if and what the duplicates are
results_df, duplicates_df = analyze_ids(gdf_s, "sampleid", "geometry")

results_mt1_geopoint = results_df[results_df['geometry_list'].apply(len) > 1]

# Display the results of the above function call
display(results_mt1_geopoint[results_mt1_geopoint['all_unique'] == True].head())
display(results_df.shape)
display(results_mt1_geopoint[results_mt1_geopoint['all_unique'] == True].shape[0])
display(results_df[results_df['all_unique'] == False].shape[0])

sampleid                                      geometry_list  all_unique
4         9  [POINT (-85.132333 9.614592000000002), POINT (...        True
5        10  [POINT (-85.132333 9.615017134355497), POINT (...        True
6        11  [POINT (-85.13190180866356 9.614166865110107),...        True
7        12  [POINT (-85.13190180866356 9.614592000000002),...        True
8        13  [POINT (-85.13190180866356 9.615017134355497),...        True

(49469, 3)

41374

63

**Recall Question 4: "Are there sampleids that are associated with **more than one** unique geometric point?"**

To answer this, we're going to analyze the `geometric` column, in the `gdf_s` dataframe, for each `sampleid` that appears **more than once**.

> Note: We are using the `geometric` column since it aggregates the longitude and latitude into a single column and data type

Taking a look at the resulting dataframe from our analysis function, we can tell that from the 49,469 unique sampleids:
- 41,374 are associated with **multiple unique** geometric points
- 63 are associated with **some duplicated** geometric points

Therefore, the answer to Question 4 is **Yes**, since 41,374 sampleids are associated with **more than one** unique geometric point.

> Question 5: Are there geometry points that are associated with **more than one** unique sampleid?

In [275]:
# This should answer Question 5: "Are there geometry points that are associated with more than one unique sampleid?"

results_df, duplicates_df = analyze_ids(gdf_s, "geometry", "sampleid")

results_mt1_sampleid = results_df[results_df['sampleid_list'].apply(len) > 1]

# Uncomment to show that there are no geometry points associated with more than two sampleids
#display(results_df[results_df['sampleid_list'].apply(len) > 2])

# Display the results of the above function call
display(results_mt1_sampleid[results_mt1_sampleid['all_unique'] == True].head())
display(results_df.shape)
display(results_mt1_sampleid[results_mt1_sampleid['all_unique'] == True].shape[0])
display(results_df[results_df['all_unique'] == False].shape[0])

geometry   sampleid_list  all_unique
36  POINT (-84.37434 9.50804)  [227, 3600227]        True
37   POINT (-84.3739 9.50804)  [230, 3600230]        True
38   POINT (-84.3739 9.50762)  [229, 3600229]        True
39  POINT (-84.37434 9.50762)  [226, 3600226]        True
40  POINT (-84.37434 9.50719)  [225, 3600225]        True

(91917, 3)

9180

63

**Recall Question 5: "Are there geometry points that are associated with more than one unique sampleid?"**

With the analysis function used previous, we can aggregate all the sampleids associated with each geometry point.

Taking a look at the resulting table, and its dimensions, we can see that of the 91,917 unique geometry points:
- 9,180 are associated with multiple **unique** sampleids
- 63 are associated with multiple **of the same** sampleids

> Note: We know this because each geometry point is only associated with **up to** two sampleids (shown by the commented code above)

In [276]:
# Figure out which rows are associated with QA/QC entries
# To do that, let's take a look at the plotids and sampleids of the duplicated geometric points

duplicated_sampleids = results_mt1_sampleid[results_mt1_sampleid['all_unique'] == True]

results_df, duplicates_df = analyze_ids(gdf_s, "geometry", "plotid")
results_mt1_plotid = results_df[results_df['plotid_list'].apply(len) > 1]
duplicated_plotids = results_mt1_plotid[results_mt1_plotid['all_unique'] == True]

# Uncomment to show that both dataframes contains the same geometric points (values in the geometry column)
#display(duplicated_sampleids['geometry'].equals(duplicated_plotids['geometry']))

qaqc_df = pd.merge(duplicated_plotids, duplicated_sampleids, how='inner', on='geometry')
qaqc_df = qaqc_df.drop(columns=['all_unique_x', 'all_unique_y'])

display(qaqc_df.head(10))
display(qaqc_df['geometry'].value_counts().reset_index()['count'].unique())
display(qaqc_df['plotid_list'].explode().value_counts().reset_index()['count'].unique())
display(qaqc_df['sampleid_list'].explode().value_counts().reset_index()['count'].unique())

geometry      plotid_list     sampleid_list
0  POINT (-84.37434 9.50804)     [57, 900057]    [227, 3600227]
1   POINT (-84.3739 9.50804)     [57, 900057]    [230, 3600230]
2   POINT (-84.3739 9.50762)     [57, 900057]    [229, 3600229]
3  POINT (-84.37434 9.50762)     [57, 900057]    [226, 3600226]
4  POINT (-84.37434 9.50719)     [57, 900057]    [225, 3600225]
5   POINT (-84.3739 9.50719)     [57, 900057]    [228, 3600228]
6  POINT (-84.37347 9.50719)     [57, 900057]    [231, 3600231]
7  POINT (-84.37347 9.50762)     [57, 900057]    [232, 3600232]
8  POINT (-84.37347 9.50804)     [57, 900057]    [233, 3600233]
9  POINT (-84.26062 9.50729)  [10231, 910231]  [40921, 3640921]

array([1])

array([9])

array([3, 2, 1])

---
Looking at the dataframe displayed, we can see all the plotids and sampleids associated with each geometric point.
> Note: As a reminder the geometric points in this dataframe are the ones that appear more than once (exactly twice) in the dataset

Empirically, we can observe that in this dataframe it seems all QA/QC entries, (NOTE), have a pattern of adding a certain amount to get the new id.
> Note: (that are not assigned the same sampleid),
- For example, 900,000 is added to the original plotid to get the new QA/QC plotid.
- In case of sampleids, it seems 3,600,000 is added.

Once we have fact-checked our empirical observation, in the next cell, we can go ahead and determine which entries to keep and which to remove.

---

The next three lines describe the frequency of each unique value in the given column, so:
- There is 1 occurance of each geometric point (as expected),
- There are 9 occurances of each plotid (as expected),
- There are 1, 2, or 3 occurances of each sampleid (**not expected**).

Based on this, it demonstrates that a lot of geometric points are being associated with sampleids used by different geometric points.
> Thought: It might be best if we went through the dataset and assigned each geometric point a unique sampleid

In [277]:
# Series of all geometry values which appear more than once
geopoints_to_check = results_mt1_sampleid['geometry']

# Check the unique number of occurrences of geometry points
print(gdf_s['geometry'].value_counts().value_counts())

# Create a new column that counts the number of NA values in the row
gdf_s['na_count'] = gdf_s.isna().sum(axis=1)

# Get all the indexes to drop based on which has the most NA values
# Note, idxmax() drops the first occurrence in the case of a tie, therefore it will drop the oldest record and keep the QA/QC one
index_to_drop = gdf_s[gdf_s['geometry'].isin(geopoints_to_check)].groupby('geometry')['na_count'].idxmax()

# Drop the entries from the GeoDataFrame (gdf_s) and (gdf_e)
gdf_s = gdf_s.drop(index=index_to_drop, errors='ignore').drop(columns=['na_count'])
gdf_e = gdf_e.drop(index=index_to_drop, errors='ignore')

# Display the new shape of the GeoDataFrame
display(gdf_s.shape)

# Check the unique number of occurrences of geometry points after we removed duplicates
print(gdf_s['geometry'].value_counts().value_counts())

count
1    82674
2     9243
Name: count, dtype: int64


(91917, 16)

count
1    91917
Name: count, dtype: int64


In [278]:
# Take a look at the NA values of every column of the dataset and determine what to do with said NA values

# Prints the NA count for column with NA values
na_count = gdf_s.isna().sum()
print(na_count)

plotid            0
sampleid          0
Uso             171
Cobertura       171
Vegetacion     6073
Herbaceas     68902
Pasto_Arb     70124
Cultivo       84108
Humedal       88258
Terreno       87077
Agua          91123
Otra_clase    87185
SAF           84108
Cambios15_      171
Gana_Perdi    88786
geometry          0
dtype: int64


Based on the data shown above, we still have a lot of columns that contain NA values.

As such, we are going to replace all the NA values in those columns with "Not_Applicable" to fix that.

In [279]:
# Columns to replace NA values
sp_columns_to_replace = ['Uso', 'Cobertura', 'Vegetacion', 'Herbaceas', 'Pasto_Arb', 'Cultivo', 'Humedal', 'Terreno', 'Agua', 'Otra_clase', 'SAF', 'Cambios15_', 'Gana_Perdi']
en_columns_to_replace = ['Use', 'CoverType', 'Vegetations', 'Herbaceous', 'GrasslandShrub', 'CropsType', 'WetlandArea', 'LandType', 'WaterBodyType', 'OtherClass', 'SAF', 'Changes_15', 'Gain_Loss']

# Replace NA values with "Not_Applicable"
gdf_s[sp_columns_to_replace] = gdf_s[sp_columns_to_replace].fillna("No_Aplicable")
gdf_e[en_columns_to_replace] = gdf_e[en_columns_to_replace].fillna("Not_Applicable")

# Prints the NA count for column with NA values, just to double check
na_count = gdf_s.isna().sum()
print(na_count)

plotid        0
sampleid      0
Uso           0
Cobertura     0
Vegetacion    0
Herbaceas     0
Pasto_Arb     0
Cultivo       0
Humedal       0
Terreno       0
Agua          0
Otra_clase    0
SAF           0
Cambios15_    0
Gana_Perdi    0
geometry      0
dtype: int64


Now that we've cleaned the data from all NA values, and removed our duplicate quality control/quality assurance entires, let's save this dataset

In [280]:
# Confirm that the changes we've been doing to gdf_s were also applied to gdf_e
na_count = gdf_e.isna().sum()
print(na_count)

print(gdf_e['geometry'].equals(gdf_s['geometry']))

plotid            0
sampleid          0
Use               0
CoverType         0
Vegetations       0
Herbaceous        0
GrasslandShrub    0
CropsType         0
WetlandArea       0
LandType          0
WaterBodyType     0
OtherClass        0
SAF               0
Changes_15        0
Gain_Loss         0
geometry          0
dtype: int64
True


In [281]:
# Saves the Spanish (original language) dataframe as a parquet file
gdf_s.to_parquet("../Costa_Rica_Data/Data Acquisition Output/classification_data/sp_clean_classification_data.parquet", engine="pyarrow")

# Saves the English (translated language) dataframe as a parquet file
gdf_e.to_parquet("../Costa_Rica_Data/Data Acquisition Output/classification_data/en_clean_classification_data.parquet", engine="pyarrow")

In [282]:
# TODO: Use the actual 10,000 row dataset instead of this makeshift version
# Map the plots (the 10,000 not the 90,000)

# Create a makeshift subset of the original GeoDataFrame
downsampled_gdf = gdf_s.iloc[::9]

# Calculate the mean geometric point to center the map
mean_point = downsampled_gdf.geometry.union_all().centroid
mean_lat, mean_lon = mean_point.y, mean_point.x

# Initialize a Folium map centered on the mean geometric point
m = folium.Map(location=[mean_lat, mean_lon], zoom_start=9)

# Add each point from the downsampled GeoDataFrame to the map
for _, row in downsampled_gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=1,  # Smaller radius for points
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.7
    ).add_to(m)

# Display the map
display(m)

Using folium, and a makeshift subset of our original dataset, this creates a map of one point per plot.